<a href="https://colab.research.google.com/github/wwoliver19/Projects/blob/main/IT7103Project_HotelRes.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install ydata-profiling

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 356.2/356.2 kB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 686.1/686.1 kB 16.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.8/104.8 kB 4.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.5/4.5 MB 31.2 MB/s eta 0:00:00
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27081 sha256=e749848d137299eb975ef4f93f038be805f2433d9a80d89db87025dcc0c57329
  Stored in directory: /root/.cache/pip/wheels/dd/91/29/a79cecb328d01739e64017b6fb9a1ab9d8cb1853098ec5966d
Successfully built htmlmin


In [2]:
import pandas as pd
from ydata_profiling import ProfileReport
import numpy as np
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import FunctionTransformer
from sklearn.preprocessing import OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.model_selection import GridSearchCV


In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
#Wesleys Path
data = pd.read_csv('/content/drive/MyDrive/KSU/IT7103Practical/Group Project/Hotel Reservations.csv')

In [5]:
data = data.drop('Booking_ID', axis=1)

In [6]:
# EDA using ydata-profiling
profile_report = ProfileReport(data, explorative=True)
profile_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [7]:
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt

traindata, testdata = train_test_split(data, test_size=0.25)
traindata.shape, testdata.shape

((27206, 18), (9069, 18))

<h2>Pipeline

In [8]:
num_cols = ['arrival_month', 'arrival_date']
log_cols = ['no_of_weekend_nights', 'no_of_week_nights', 'no_of_children', 'lead_time', 'no_of_special_requests']
cat_cols = ['type_of_meal_plan', 'required_car_parking_space', 'room_type_reserved']
target = 'booking_status'


from sklearn.preprocessing import OneHotEncoder, FunctionTransformer
from sklearn.compose import ColumnTransformer
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

num_pipeline = Pipeline([
    ('impute', SimpleImputer(strategy='median')),
    ('standardize', StandardScaler())
])

def log_transformation(x):
    return np.log(x+0.1)

log_pipeline = Pipeline([
    ('impute', SimpleImputer(strategy='median')),
    ('log transform', FunctionTransformer(log_transformation)),
    ('standardize', StandardScaler())
])

processing_pipeline = ColumnTransformer([
    ('numeric', num_pipeline, num_cols),
    ('log', log_pipeline, log_cols),
    ('class', OneHotEncoder(max_categories=5, handle_unknown='infrequent_if_exist'), cat_cols)

])

<h2>Logistic Regression

In [9]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score




In [10]:
logistic_pipeline = Pipeline([
    ('processing', processing_pipeline),
    ('logistic', LogisticRegression(max_iter=1000))
])

param_grid = [{
    'logistic__C': [1]
}]

grid_search = GridSearchCV(logistic_pipeline, param_grid, cv=5, scoring='accuracy', return_train_score=True)
grid_search.fit(traindata, traindata[target])

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('processing',
                                        ColumnTransformer(transformers=[('numeric',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('standardize',
                                                                                          StandardScaler())]),
                                                                         ['arrival_month',
                                                                          'arrival_date']),
                                                                        ('log',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('log '
                                                                                          'transform',
                                                                                          FunctionTransformer(func=<function l...
                                                                          'no_of_week_nights',
                                                                          'no_of_children',
                                                                          'lead_time',
                                                                          'no_of_special_requests']),
                                                                        ('class',
                                                                         OneHotEncoder(handle_unknown='infrequent_if_exist',
                                                                                       max_categories=5),
                                                                         ['type_of_meal_plan',
                                                                          'required_car_parking_space',
                                                                          'room_type_reserved'])])),
                                       ('logistic',
                                        LogisticRegression(max_iter=1000))]),
             param_grid=[{'logistic__C': [1]}], return_train_score=True,
             scoring='accuracy')

In [11]:
print('Best logistic regression hyperparameters: ', grid_search.best_params_)
print('Best score against train data:', grid_search.best_score_)
grid_search.score(testdata, testdata[target])

Best logistic regression hyperparameters:  {'logistic__C': 1}
Best score against train data: 0.7575165986590575


0.7560921821590032

<h2>Decision Tree

In [12]:
from sklearn.model_selection import GridSearchCV
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score

dtc = Pipeline([
    ('processing', processing_pipeline),
    ('dtc',DecisionTreeClassifier())
])

In [13]:
param_grid = {
    'dtc__max_depth' : [6],
    'dtc__min_samples_split' : [0.000015],
    'dtc__min_samples_leaf' : [0.0015],
    'dtc__max_features' : [None],
    'dtc__max_leaf_nodes' : [None]
}

grid_search = GridSearchCV(dtc, param_grid, cv=5, scoring='accuracy', return_train_score=True)
grid_search.fit(traindata, traindata[target])

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('processing',
                                        ColumnTransformer(transformers=[('numeric',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('standardize',
                                                                                          StandardScaler())]),
                                                                         ['arrival_month',
                                                                          'arrival_date']),
                                                                        ('log',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('log '
                                                                                          'transform',
                                                                                          FunctionTransformer(func=<function l...
                                                                         OneHotEncoder(handle_unknown='infrequent_if_exist',
                                                                                       max_categories=5),
                                                                         ['type_of_meal_plan',
                                                                          'required_car_parking_space',
                                                                          'room_type_reserved'])])),
                                       ('dtc', DecisionTreeClassifier())]),
             param_grid={'dtc__max_depth': [6], 'dtc__max_features': [None],
                         'dtc__max_leaf_nodes': [None],
                         'dtc__min_samples_leaf': [0.0015],
                         'dtc__min_samples_split': [1.5e-05]},
             return_train_score=True, scoring='accuracy')

In [14]:
print('Best decision tree hyperparameters: ', grid_search.best_params_)
print('Best score against train data:', grid_search.best_score_)
grid_search.score(testdata, testdata[target])

Best decision tree hyperparameters:  {'dtc__max_depth': 6, 'dtc__max_features': None, 'dtc__max_leaf_nodes': None, 'dtc__min_samples_leaf': 0.0015, 'dtc__min_samples_split': 1.5e-05}
Best score against train data: 0.7855986449407061


0.7782555959863271

<h2>Random Forest

In [15]:
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier

rfc = Pipeline([
    ('processing', processing_pipeline),
    ('rfc', RandomForestClassifier())
])

In [16]:
param_grid = [{
    'rfc__n_estimators' : [35],
    'rfc__max_depth' : [4],
    'rfc__min_samples_split' : [0.2],
    'rfc__min_samples_leaf' : [0.1],
    'rfc__max_features' : [0.75],
    'rfc__max_leaf_nodes' : [None]
}]

grid_search = GridSearchCV(rfc, param_grid, cv=3, scoring='accuracy', return_train_score=True)
grid_search.fit(traindata, traindata[target])

GridSearchCV(cv=3,
             estimator=Pipeline(steps=[('processing',
                                        ColumnTransformer(transformers=[('numeric',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('standardize',
                                                                                          StandardScaler())]),
                                                                         ['arrival_month',
                                                                          'arrival_date']),
                                                                        ('log',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('log '
                                                                                          'transform',
                                                                                          FunctionTransformer(func=<function l...
                                                                                       max_categories=5),
                                                                         ['type_of_meal_plan',
                                                                          'required_car_parking_space',
                                                                          'room_type_reserved'])])),
                                       ('rfc', RandomForestClassifier())]),
             param_grid=[{'rfc__max_depth': [4], 'rfc__max_features': [0.75],
                          'rfc__max_leaf_nodes': [None],
                          'rfc__min_samples_leaf': [0.1],
                          'rfc__min_samples_split': [0.2],
                          'rfc__n_estimators': [35]}],
             return_train_score=True, scoring='accuracy')

In [17]:
print('Best random forest hyperparameters: ', grid_search.best_params_)
print('Best score against train data:', grid_search.best_score_)
grid_search.score(testdata, testdata[target])

Best random forest hyperparameters:  {'rfc__max_depth': 4, 'rfc__max_features': 0.75, 'rfc__max_leaf_nodes': None, 'rfc__min_samples_leaf': 0.1, 'rfc__min_samples_split': 0.2, 'rfc__n_estimators': 35}
Best score against train data: 0.7610819176848169


0.7579666997463888

<h2>Gradient Boosting

In [18]:
from sklearn.ensemble import GradientBoostingClassifier

gbc = Pipeline([
    ('processing', processing_pipeline),
    ('gbc', GradientBoostingClassifier())
])

In [19]:
param_grid = [{
    'gbc__n_estimators' : [150],
    'gbc__max_depth' : [8],
    'gbc__min_samples_split' : [0.05],
    'gbc__min_samples_leaf' : [0.001],
    'gbc__max_features' : [0.75],
    'gbc__max_leaf_nodes' : [None]
}]

grid_search = GridSearchCV(gbc, param_grid, cv=3, scoring='accuracy', return_train_score=True)
grid_search.fit(traindata, traindata[target])

GridSearchCV(cv=3,
             estimator=Pipeline(steps=[('processing',
                                        ColumnTransformer(transformers=[('numeric',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('standardize',
                                                                                          StandardScaler())]),
                                                                         ['arrival_month',
                                                                          'arrival_date']),
                                                                        ('log',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('log '
                                                                                          'transform',
                                                                                          FunctionTransformer(func=<function l...
                                                                                       max_categories=5),
                                                                         ['type_of_meal_plan',
                                                                          'required_car_parking_space',
                                                                          'room_type_reserved'])])),
                                       ('gbc', GradientBoostingClassifier())]),
             param_grid=[{'gbc__max_depth': [8], 'gbc__max_features': [0.75],
                          'gbc__max_leaf_nodes': [None],
                          'gbc__min_samples_leaf': [0.001],
                          'gbc__min_samples_split': [0.05],
                          'gbc__n_estimators': [150]}],
             return_train_score=True, scoring='accuracy')

In [20]:
print('Best gradient boosting hyperparameters: ', grid_search.best_params_)
print('Best score against train data:', grid_search.best_score_)
grid_search.score(testdata, testdata[target])

Best gradient boosting hyperparameters:  {'gbc__max_depth': 8, 'gbc__max_features': 0.75, 'gbc__max_leaf_nodes': None, 'gbc__min_samples_leaf': 0.001, 'gbc__min_samples_split': 0.05, 'gbc__n_estimators': 150}
Best score against train data: 0.8300742762414425


0.8282059764031315

<h2>Support Vector Machine

In [21]:
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVC

svc = Pipeline([
    ('processing', processing_pipeline),
    ('svc', SVC())
])

In [22]:
param_grid = [
    {'svc__kernel':['linear'],
     'svc__C' : [1]},
    {'svc__kernel':['poly'],
     'svc__degree' : [3],
     'svc__C' : [1]},
    {'svc__kernel':['rbf'],
     'svc__gamma' : [1],
     'svc__C' : [1]}
]

grid_search = GridSearchCV(svc, param_grid, cv=3, scoring='accuracy', return_train_score=True)
grid_search.fit(traindata, traindata[target])

GridSearchCV(cv=3,
             estimator=Pipeline(steps=[('processing',
                                        ColumnTransformer(transformers=[('numeric',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('standardize',
                                                                                          StandardScaler())]),
                                                                         ['arrival_month',
                                                                          'arrival_date']),
                                                                        ('log',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('log '
                                                                                          'transform',
                                                                                          FunctionTransformer(func=<function l...
                                                                         OneHotEncoder(handle_unknown='infrequent_if_exist',
                                                                                       max_categories=5),
                                                                         ['type_of_meal_plan',
                                                                          'required_car_parking_space',
                                                                          'room_type_reserved'])])),
                                       ('svc', SVC())]),
             param_grid=[{'svc__C': [1], 'svc__kernel': ['linear']},
                         {'svc__C': [1], 'svc__degree': [3],
                          'svc__kernel': ['poly']},
                         {'svc__C': [1], 'svc__gamma': [1],
                          'svc__kernel': ['rbf']}],
             return_train_score=True, scoring='accuracy')

In [23]:
print('Best support vector machine hyperparameters: ', grid_search.best_params_)
print('Best score against train data:', grid_search.best_score_)
grid_search.score(testdata, testdata[target])

Best support vector machine hyperparameters:  {'svc__C': 1, 'svc__gamma': 1, 'svc__kernel': 'rbf'}
Best score against train data: 0.818128237353743


0.8185025912449002

<h2>Stochastic Gradient Descent

In [24]:
from sklearn.pipeline import Pipeline
from sklearn.linear_model import SGDClassifier

sgd = Pipeline([
    ('processing', processing_pipeline),
    ('sgd', SGDClassifier())
])

In [25]:
param_grid = {
    'sgd__loss': ['log_loss'],
    'sgd__alpha': [0.001],
    'sgd__penalty': ['l1'],
    'sgd__max_iter': [1000],
    'sgd__eta0': [1]
}

grid_search = GridSearchCV(sgd, param_grid, cv=3, scoring='accuracy', return_train_score=True)
grid_search.fit(traindata, traindata[target])

GridSearchCV(cv=3,
             estimator=Pipeline(steps=[('processing',
                                        ColumnTransformer(transformers=[('numeric',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('standardize',
                                                                                          StandardScaler())]),
                                                                         ['arrival_month',
                                                                          'arrival_date']),
                                                                        ('log',
                                                                         Pipeline(steps=[('impute',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('log '
                                                                                          'transform',
                                                                                          FunctionTransformer(func=<function l...
                                                                          'no_of_special_requests']),
                                                                        ('class',
                                                                         OneHotEncoder(handle_unknown='infrequent_if_exist',
                                                                                       max_categories=5),
                                                                         ['type_of_meal_plan',
                                                                          'required_car_parking_space',
                                                                          'room_type_reserved'])])),
                                       ('sgd', SGDClassifier())]),
             param_grid={'sgd__alpha': [0.001], 'sgd__eta0': [1],
                         'sgd__loss': ['log_loss'], 'sgd__max_iter': [1000],
                         'sgd__penalty': ['l1']},
             return_train_score=True, scoring='accuracy')

In [26]:
print('Best stochastic gradient descent hyperparameters: ', grid_search.best_params_)
print('Best score against train data:', grid_search.best_score_)
grid_search.score(testdata, testdata[target])

Best stochastic gradient descent hyperparameters:  {'sgd__alpha': 0.001, 'sgd__eta0': 1, 'sgd__loss': 'log_loss', 'sgd__max_iter': 1000, 'sgd__penalty': 'l1'}
Best score against train data: 0.7576637729570525


0.7556511191972655